In [65]:
import scipy.io as sio
import numpy as np
import pandas as pd
import torch
import os
from glob import glob
import torch
import torch.nn as nn
import torch.nn.functional as F
from torchvision import datasets,transforms
dependencies = ['torch']
import matplotlib.ticker as ticker
import numpy as np
from time import time
from matplotlib import pyplot as plt
import random
from scipy import fftpack
from glob import glob
import sys

from torch.autograd import Variable
import math

torch.cuda.set_device(0)
torch.cuda.empty_cache()
rd_seed=2#5100,5101,
torch.manual_seed(rd_seed)
torch.cuda.manual_seed(rd_seed)
torch.cuda.manual_seed_all(rd_seed)
np.random.seed(rd_seed)
torch.backends.cudnn.deterministic =True

plt.style.use('ggplot')

In [4]:
raw_data_list=glob("./training2017/*.mat*")
raw_data_list.sort()
raw_data_list

['./training2017\\A00001.mat',
 './training2017\\A00002.mat',
 './training2017\\A00003.mat',
 './training2017\\A00004.mat',
 './training2017\\A00005.mat',
 './training2017\\A00006.mat',
 './training2017\\A00007.mat',
 './training2017\\A00008.mat',
 './training2017\\A00009.mat',
 './training2017\\A00010.mat',
 './training2017\\A00011.mat',
 './training2017\\A00012.mat',
 './training2017\\A00013.mat',
 './training2017\\A00014.mat',
 './training2017\\A00015.mat',
 './training2017\\A00016.mat',
 './training2017\\A00017.mat',
 './training2017\\A00018.mat',
 './training2017\\A00019.mat',
 './training2017\\A00020.mat',
 './training2017\\A00021.mat',
 './training2017\\A00022.mat',
 './training2017\\A00023.mat',
 './training2017\\A00024.mat',
 './training2017\\A00025.mat',
 './training2017\\A00026.mat',
 './training2017\\A00027.mat',
 './training2017\\A00028.mat',
 './training2017\\A00029.mat',
 './training2017\\A00030.mat',
 './training2017\\A00031.mat',
 './training2017\\A00032.mat',
 './trai

In [39]:
Fs=300#Hz
resample_Fs = 80#Hz
seg_len=256 #dot
seg_time=seg_len/resample_Fs
raw_seg_len=int(seg_time*Fs)
print(seg_time)


3.2
tensor([-127., -162., -197., -229., -245., -254., -261., -265., -268., -268.]) torch.Size([9000])


tensor([[[-127., -162., -197.,  ...,    0.,   -1.,   -2.],
         [  -3.,   -4.,   -6.,  ...,    2.,    5.,    7.],
         [   7.,    7.,    6.,  ...,  -15.,  -14.,  -11.],
         ...,
         [  -5.,    9.,   19.,  ...,  -46.,  -42.,  -38.],
         [ -36.,  -34.,  -32.,  ...,  -45.,  -48.,  -50.],
         [ -53.,  -54.,  -50.,  ...,   -2.,    2.,    6.]]])

In [43]:
tmp.split('\\')[-1].split('.')[0]

'A00001'

In [61]:
lab_file=pd.read_table('REFERENCE-v3.csv',header=None,sep=',',names=['DtIdx','Label'])
lab_dict={}
for dt_idx,lab_idx in zip(lab_file['DtIdx'].values,lab_file['Label'].values):
    lab_dict[dt_idx]=lab_idx
lab_dict

{'A00001': 'N',
 'A00002': 'N',
 'A00003': 'N',
 'A00004': 'A',
 'A00005': 'A',
 'A00006': 'N',
 'A00007': 'N',
 'A00008': 'O',
 'A00009': 'A',
 'A00010': 'N',
 'A00011': 'N',
 'A00012': 'N',
 'A00013': 'O',
 'A00014': 'N',
 'A00015': 'A',
 'A00016': 'N',
 'A00017': 'O',
 'A00018': 'N',
 'A00019': 'N',
 'A00020': 'O',
 'A00021': 'N',
 'A00022': '~',
 'A00023': 'O',
 'A00024': 'O',
 'A00025': 'N',
 'A00026': 'N',
 'A00027': 'A',
 'A00028': 'N',
 'A00029': 'O',
 'A00030': 'O',
 'A00031': 'N',
 'A00032': 'N',
 'A00033': 'N',
 'A00034': '~',
 'A00035': 'N',
 'A00036': 'N',
 'A00037': 'N',
 'A00038': 'O',
 'A00039': 'N',
 'A00040': 'N',
 'A00041': 'O',
 'A00042': 'N',
 'A00043': 'O',
 'A00044': 'N',
 'A00045': 'N',
 'A00046': 'N',
 'A00047': 'O',
 'A00048': 'N',
 'A00049': 'N',
 'A00050': 'N',
 'A00051': 'N',
 'A00052': 'N',
 'A00053': 'N',
 'A00054': 'A',
 'A00055': 'O',
 'A00056': '~',
 'A00057': 'N',
 'A00058': 'O',
 'A00059': 'N',
 'A00060': 'N',
 'A00061': 'O',
 'A00062': 'N',
 'A00063

In [74]:
for dt_file in raw_data_list:
    dt=sio.loadmat(dt_file)
    dt_tensor=torch.FloatTensor(dt['val']).squeeze()
    print(dt_tensor[0:10],dt_tensor.shape)
    num_epoch=(len(dt_tensor)//raw_seg_len)
    print(num_epoch)
    dt_tensor=dt_tensor[0:num_epoch*raw_seg_len]
    dt_tensor=dt_tensor.reshape(num_epoch,-1).unsqueeze(dim=0)

    rs_dt_tensor=torch.nn.functional.interpolate(dt_tensor, size=seg_len, mode='linear', align_corners=True).squeeze()
    rs_dt=rs_dt_tensor.numpy()
    print(rs_dt.shape)
    seg_root_path="./Seg/"
    print(seg_root_path)
    dt_index=dt_file.split('\\')[-1].split('.')[0]
    if not os.path.exists(seg_root_path):
        os.makedirs(seg_root_path)

    for idx in range(num_epoch):
        dt_path=seg_root_path+lab_dict[dt_index]+'_'+dt_index+"_%.0f.npy"%(idx)
        print(dt_path,rs_dt[idx].shape)
        np.save(dt_path,rs_dt[idx])

tensor([-127., -162., -197., -229., -245., -254., -261., -265., -268., -268.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A00001_0.npy (256,)
./Seg/N_A00001_1.npy (256,)
./Seg/N_A00001_2.npy (256,)
./Seg/N_A00001_3.npy (256,)
./Seg/N_A00001_4.npy (256,)
./Seg/N_A00001_5.npy (256,)
./Seg/N_A00001_6.npy (256,)
./Seg/N_A00001_7.npy (256,)
./Seg/N_A00001_8.npy (256,)
tensor([128., 157., 189., 226., 250., 257., 262., 265., 268., 269.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A00002_0.npy (256,)
./Seg/N_A00002_1.npy (256,)
./Seg/N_A00002_2.npy (256,)
./Seg/N_A00002_3.npy (256,)
./Seg/N_A00002_4.npy (256,)
./Seg/N_A00002_5.npy (256,)
./Seg/N_A00002_6.npy (256,)
./Seg/N_A00002_7.npy (256,)
./Seg/N_A00002_8.npy (256,)
tensor([ 56.,  73.,  85.,  93., 100., 107., 113., 117., 118., 117.]) torch.Size([18000])
18
(18, 256)
./Seg/
./Seg/N_A00003_0.npy (256,)
./Seg/N_A00003_1.npy (256,)
./Seg/N_A00003_2.npy (256,)
./Seg/N_A00003_3.npy (256,)
./Seg/N_A00003_4.npy (256,)
./Seg/N_A00003_5.npy (256

./Seg/O_A00030_2.npy (256,)
./Seg/O_A00030_3.npy (256,)
./Seg/O_A00030_4.npy (256,)
./Seg/O_A00030_5.npy (256,)
./Seg/O_A00030_6.npy (256,)
./Seg/O_A00030_7.npy (256,)
./Seg/O_A00030_8.npy (256,)
./Seg/O_A00030_9.npy (256,)
./Seg/O_A00030_10.npy (256,)
./Seg/O_A00030_11.npy (256,)
./Seg/O_A00030_12.npy (256,)
./Seg/O_A00030_13.npy (256,)
./Seg/O_A00030_14.npy (256,)
./Seg/O_A00030_15.npy (256,)
./Seg/O_A00030_16.npy (256,)
./Seg/O_A00030_17.npy (256,)
tensor([ 37.,  53.,  67.,  85., 106., 125., 140., 153., 166., 178.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A00031_0.npy (256,)
./Seg/N_A00031_1.npy (256,)
./Seg/N_A00031_2.npy (256,)
./Seg/N_A00031_3.npy (256,)
./Seg/N_A00031_4.npy (256,)
./Seg/N_A00031_5.npy (256,)
./Seg/N_A00031_6.npy (256,)
./Seg/N_A00031_7.npy (256,)
./Seg/N_A00031_8.npy (256,)
tensor([417., 496., 572., 639., 676., 689., 662., 616., 572., 511.]) torch.Size([8694])
9
(9, 256)
./Seg/
./Seg/N_A00032_0.npy (256,)
./Seg/N_A00032_1.npy (256,)
./Seg/N_A00032_2.npy (25

./Seg/N_A00060_2.npy (256,)
./Seg/N_A00060_3.npy (256,)
./Seg/N_A00060_4.npy (256,)
./Seg/N_A00060_5.npy (256,)
./Seg/N_A00060_6.npy (256,)
./Seg/N_A00060_7.npy (256,)
./Seg/N_A00060_8.npy (256,)
./Seg/N_A00060_9.npy (256,)
./Seg/N_A00060_10.npy (256,)
./Seg/N_A00060_11.npy (256,)
./Seg/N_A00060_12.npy (256,)
./Seg/N_A00060_13.npy (256,)
tensor([224., 260., 304., 339., 358., 372., 377., 370., 356., 345.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/O_A00061_0.npy (256,)
./Seg/O_A00061_1.npy (256,)
./Seg/O_A00061_2.npy (256,)
./Seg/O_A00061_3.npy (256,)
./Seg/O_A00061_4.npy (256,)
./Seg/O_A00061_5.npy (256,)
./Seg/O_A00061_6.npy (256,)
./Seg/O_A00061_7.npy (256,)
./Seg/O_A00061_8.npy (256,)
tensor([-140., -205., -270., -273., -244., -244., -269., -260., -206., -205.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A00062_0.npy (256,)
./Seg/N_A00062_1.npy (256,)
./Seg/N_A00062_2.npy (256,)
./Seg/N_A00062_3.npy (256,)
./Seg/N_A00062_4.npy (256,)
./Seg/N_A00062_5.npy (256,)
./Seg/N_A00062_6.n

./Seg/N_A00089_6.npy (256,)
./Seg/N_A00089_7.npy (256,)
./Seg/N_A00089_8.npy (256,)
tensor([ -93., -130., -173., -215., -258., -298., -328., -350., -369., -387.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/A_A00090_0.npy (256,)
./Seg/A_A00090_1.npy (256,)
./Seg/A_A00090_2.npy (256,)
./Seg/A_A00090_3.npy (256,)
./Seg/A_A00090_4.npy (256,)
./Seg/A_A00090_5.npy (256,)
./Seg/A_A00090_6.npy (256,)
./Seg/A_A00090_7.npy (256,)
./Seg/A_A00090_8.npy (256,)
tensor([  94.,  105.,  114.,  123.,  125.,  115.,   84.,   13.,  -70., -163.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A00091_0.npy (256,)
./Seg/N_A00091_1.npy (256,)
./Seg/N_A00091_2.npy (256,)
./Seg/N_A00091_3.npy (256,)
./Seg/N_A00091_4.npy (256,)
./Seg/N_A00091_5.npy (256,)
./Seg/N_A00091_6.npy (256,)
./Seg/N_A00091_7.npy (256,)
./Seg/N_A00091_8.npy (256,)
tensor([189., 235., 288., 343., 395., 421., 440., 467., 492., 508.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/O_A00092_0.npy (256,)
./Seg/O_A00092_1.npy (256,)
./Seg/O_A00092_2.n

(9, 256)
./Seg/
./Seg/O_A00121_0.npy (256,)
./Seg/O_A00121_1.npy (256,)
./Seg/O_A00121_2.npy (256,)
./Seg/O_A00121_3.npy (256,)
./Seg/O_A00121_4.npy (256,)
./Seg/O_A00121_5.npy (256,)
./Seg/O_A00121_6.npy (256,)
./Seg/O_A00121_7.npy (256,)
./Seg/O_A00121_8.npy (256,)
tensor([ -35.,  -73.,  -97., -117., -139., -150., -157., -162., -167., -170.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A00122_0.npy (256,)
./Seg/N_A00122_1.npy (256,)
./Seg/N_A00122_2.npy (256,)
./Seg/N_A00122_3.npy (256,)
./Seg/N_A00122_4.npy (256,)
./Seg/N_A00122_5.npy (256,)
./Seg/N_A00122_6.npy (256,)
./Seg/N_A00122_7.npy (256,)
./Seg/N_A00122_8.npy (256,)
tensor([ -23.,  -53.,  -79., -111., -147., -187., -210., -221., -230., -238.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/O_A00123_0.npy (256,)
./Seg/O_A00123_1.npy (256,)
./Seg/O_A00123_2.npy (256,)
./Seg/O_A00123_3.npy (256,)
./Seg/O_A00123_4.npy (256,)
./Seg/O_A00123_5.npy (256,)
./Seg/O_A00123_6.npy (256,)
./Seg/O_A00123_7.npy (256,)
./Seg/O_A00123_8.npy (25

...

./Seg/N_A08382_6.npy (256,)
tensor([ -8.,  -9., -11., -12., -13., -14., -16., -18., -26., -36.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/O_A08383_0.npy (256,)
./Seg/O_A08383_1.npy (256,)
./Seg/O_A08383_2.npy (256,)
./Seg/O_A08383_3.npy (256,)
./Seg/O_A08383_4.npy (256,)
./Seg/O_A08383_5.npy (256,)
./Seg/O_A08383_6.npy (256,)
./Seg/O_A08383_7.npy (256,)
./Seg/O_A08383_8.npy (256,)
tensor([116., 149., 185., 224., 244., 251., 257., 262., 265., 266.]) torch.Size([4136])
4
(4, 256)
./Seg/
./Seg/N_A08384_0.npy (256,)
./Seg/N_A08384_1.npy (256,)
./Seg/N_A08384_2.npy (256,)
./Seg/N_A08384_3.npy (256,)
tensor([ -87.,  -95., -100., -103., -102.,  -96.,  -87.,  -76.,  -62.,  -43.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08385_0.npy (256,)
./Seg/N_A08385_1.npy (256,)
./Seg/N_A08385_2.npy (256,)
./Seg/N_A08385_3.npy (256,)
./Seg/N_A08385_4.npy (256,)
./Seg/N_A08385_5.npy (256,)
./Seg/N_A08385_6.npy (256,)
./Seg/N_A08385_7.npy (256,)
./Seg/N_A08385_8.npy (256,)
tensor([-439., -527., -617.,

./Seg/N_A08420_6.npy (256,)
./Seg/N_A08420_7.npy (256,)
./Seg/N_A08420_8.npy (256,)
tensor([-151., -190., -228., -264., -291., -301., -306., -309., -311., -313.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08421_0.npy (256,)
./Seg/N_A08421_1.npy (256,)
./Seg/N_A08421_2.npy (256,)
./Seg/N_A08421_3.npy (256,)
./Seg/N_A08421_4.npy (256,)
./Seg/N_A08421_5.npy (256,)
./Seg/N_A08421_6.npy (256,)
./Seg/N_A08421_7.npy (256,)
./Seg/N_A08421_8.npy (256,)
tensor([-166., -199., -235., -275., -293., -296., -299., -300., -300., -300.]) torch.Size([3252])
3
(3, 256)
./Seg/
./Seg/A_A08422_0.npy (256,)
./Seg/A_A08422_1.npy (256,)
./Seg/A_A08422_2.npy (256,)
tensor([ -774.,  -938., -1102., -1259., -1386., -1445., -1442., -1406., -1382.,
        -1355.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08423_0.npy (256,)
./Seg/N_A08423_1.npy (256,)
./Seg/N_A08423_2.npy (256,)
./Seg/N_A08423_3.npy (256,)
./Seg/N_A08423_4.npy (256,)
./Seg/N_A08423_5.npy (256,)
./Seg/N_A08423_6.npy (256,)
./Seg/N_A08423_7.n

./Seg/N_A08446_6.npy (256,)
./Seg/N_A08446_7.npy (256,)
./Seg/N_A08446_8.npy (256,)
tensor([140., 167., 196., 218., 228., 234., 238., 240., 241., 238.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08447_0.npy (256,)
./Seg/N_A08447_1.npy (256,)
./Seg/N_A08447_2.npy (256,)
./Seg/N_A08447_3.npy (256,)
./Seg/N_A08447_4.npy (256,)
./Seg/N_A08447_5.npy (256,)
./Seg/N_A08447_6.npy (256,)
./Seg/N_A08447_7.npy (256,)
./Seg/N_A08447_8.npy (256,)
tensor([ 82.,  95., 104., 109., 107., 100.,  89.,  74.,  53.,  39.]) torch.Size([7516])
7
(7, 256)
./Seg/
./Seg/N_A08448_0.npy (256,)
./Seg/N_A08448_1.npy (256,)
./Seg/N_A08448_2.npy (256,)
./Seg/N_A08448_3.npy (256,)
./Seg/N_A08448_4.npy (256,)
./Seg/N_A08448_5.npy (256,)
./Seg/N_A08448_6.npy (256,)
tensor([ 96., 116., 128., 136., 144., 149., 153., 154., 154., 151.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08449_0.npy (256,)
./Seg/N_A08449_1.npy (256,)
./Seg/N_A08449_2.npy (256,)
./Seg/N_A08449_3.npy (256,)
./Seg/N_A08449_4.npy (256,)
./Seg/N_A0

tensor([-41., -52., -59., -65., -71., -75., -77., -74., -66., -58.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08476_0.npy (256,)
./Seg/N_A08476_1.npy (256,)
./Seg/N_A08476_2.npy (256,)
./Seg/N_A08476_3.npy (256,)
./Seg/N_A08476_4.npy (256,)
./Seg/N_A08476_5.npy (256,)
./Seg/N_A08476_6.npy (256,)
./Seg/N_A08476_7.npy (256,)
./Seg/N_A08476_8.npy (256,)
tensor([309., 365., 423., 445., 458., 467., 441., 397., 358., 333.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08477_0.npy (256,)
./Seg/N_A08477_1.npy (256,)
./Seg/N_A08477_2.npy (256,)
./Seg/N_A08477_3.npy (256,)
./Seg/N_A08477_4.npy (256,)
./Seg/N_A08477_5.npy (256,)
./Seg/N_A08477_6.npy (256,)
./Seg/N_A08477_7.npy (256,)
./Seg/N_A08477_8.npy (256,)
tensor([-142., -170., -199., -217., -223., -225., -227., -228., -230., -231.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/O_A08478_0.npy (256,)
./Seg/O_A08478_1.npy (256,)
./Seg/O_A08478_2.npy (256,)
./Seg/O_A08478_3.npy (256,)
./Seg/O_A08478_4.npy (256,)
./Seg/O_A08478_5.npy (256,)


./Seg/O_A08504_1.npy (256,)
./Seg/O_A08504_2.npy (256,)
./Seg/O_A08504_3.npy (256,)
./Seg/O_A08504_4.npy (256,)
./Seg/O_A08504_5.npy (256,)
./Seg/O_A08504_6.npy (256,)
./Seg/O_A08504_7.npy (256,)
./Seg/O_A08504_8.npy (256,)
tensor([-343., -355., -363., -346., -293., -198.,  -27.,  158.,  301.,  439.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08505_0.npy (256,)
./Seg/N_A08505_1.npy (256,)
./Seg/N_A08505_2.npy (256,)
./Seg/N_A08505_3.npy (256,)
./Seg/N_A08505_4.npy (256,)
./Seg/N_A08505_5.npy (256,)
./Seg/N_A08505_6.npy (256,)
./Seg/N_A08505_7.npy (256,)
./Seg/N_A08505_8.npy (256,)
tensor([ 599.,  738.,  894., 1022., 1114., 1192., 1225., 1244., 1258., 1279.]) torch.Size([9000])
9
(9, 256)
./Seg/
./Seg/N_A08506_0.npy (256,)
./Seg/N_A08506_1.npy (256,)
./Seg/N_A08506_2.npy (256,)
./Seg/N_A08506_3.npy (256,)
./Seg/N_A08506_4.npy (256,)
./Seg/N_A08506_5.npy (256,)
./Seg/N_A08506_6.npy (256,)
./Seg/N_A08506_7.npy (256,)
./Seg/N_A08506_8.npy (256,)
tensor([ 549.,  654.,  762.,  873.,  967